# Transmission - Reception - Plasma Storage Manager - MS Writing 

This is a standalone test of the transmission and reception. Essentially this is an extended unit test from the CBF-SDP Emulator package. It has been written to layout the requirements for the tests in a configurable way.
Also note the command lines required are printed - so you can just run the various commands by hand if you want to.

Essentially this notebook meets the acceptance criteria for YAN-742 it:

Deploys the plasma store
Deploys receiver that can write to the store
Deploys a plasma processor that can write a  measurement set that can be imaged.
Performs all this in an AA0.5 configuration

## Installation

We are assuming you have the emulator installed together with the plasma extensions. I found everything in the documentation except this issue - libplasma-dev requires some non-free packages

```
echo deb http://deb.debian.org/debian $(lsb_release --codename --short) contrib | tee /etc/apt/sources.list.d/contrib.list
echo deb http://deb.debian.org/debian $(lsb_release --codename --short) non-free | tee /etc/apt/sources.list.d/non-free.list

apt update

```


## Running

We are going to run the transmitter - the receiver - the plasma store and the MS-Writer from the same notebook - which requires some exotic asynchronous python and therefore a number of cores to run. Which is really tricky in a notebook - so we are going to use sub-process and the entry points (emu-send and emu-recv) instead of the routines themselves. 

This is a bit clumsy but should test the functionality desired. We are also going to run at AA0.5 rate - which is 13k channels - requiring a lot of open ports. Please ensure you have at least 4 spare CPU on your test machine. Running this on a loaded machine will probably result in some dropped SPEAD HEAPS - but this would be a test of the system resilience.

The work directories and test files are all inside the cbf-sdp-emulator directory - so lets check we are in the correct place - this directory is essentially where I unpacked the cdf repository to:

In [1]:
%cd /data/soft/cbf-sdp-emulator

/data/soft/cbf-sdp-emulator


### The Configuration

This is convenience functions for the configuration feel free to edit this. One new feature of note is the num_repeats parameter. This now repeats the send for the number repeats. So you can essentially run indefinitely. 


FIXME: THe receiver is still using the "old" fakeTM model. Therefore the output measurement set will not grow as the rows are being replicated. One feature to be added for PI-12 is to fix this.

In [2]:
def _get_config(channels_per_stream, rate, inputfile,outputfile):
    
    
    conf = """
    [reception]
    method  = spead2_receivers
    receiver_port_start = 41001
    datamodel = %s
    ring_heaps = 128
    outputfilename = %s
    consumer = plasma_writer
    plasma_path = /tmp/plasma
    [transmission]
    method = spead2_transmitters
    target_host = 127.0.0.1
    target_port_start = 41001
    channels_per_stream = %d 
    rate = %d
    time_interval =  0
    [reader]
    num_repeats = 1
    num_timestamps = 0
    num_channels = 0
    """ % (inputfile,outputfile,channels_per_stream,rate)
    
    return conf

This is where you can set the file and the rate at which you want to send. For quick tests just use the sim-vis.ms. WHich is 4 channels and you can send it with a single stream (CHANNELS_PER_STREAM = 4 and NUM_STREAMS = 1). The rate is in bytes/second per stream. So I tend to set it to 1GB/NUM_STREAMS - which is essential 8Gb/s.

In [3]:

#For simple quick tests

INPUT_FILE="data/sim-vis.ms"
CHANNELS_PER_STREAM = 4
NUM_STREAMS = 1

#For AA0.5LOW tests
#INPUT_FILE="data/AA05LOW.ms"
#CHANNELS_PER_STREAM = 144
#NUM_STREAMS = 96

RATE = int(1e9/NUM_STREAMS)


OUTPUT_FILE="/tmp/new-plasma.ms"
import tempfile

configfile = tempfile.mktemp(suffix='.conf', prefix='test_')


import configparser

conf = configparser.ConfigParser()
conf.read_string(_get_config(CHANNELS_PER_STREAM, RATE, INPUT_FILE, OUTPUT_FILE))

with open(configfile,"w") as f:
    conf.write(f)

    

### Launching the plasma store

This just launches the default store with a GB of storage attached to /tmp/plasma

### We need a process to attach to the store and do something

For this we use the plasma writer. Which just pulls the visblocks out of the store and writes them to a measurement set

In [4]:
import subprocess as sp
import time

command_line = ["plasma_store","-m","1000000000","-s","/tmp/plasma"]
print(command_line)
store = sp.Popen(command_line)

time.sleep(5)

['plasma_store', '-m', '1000000000', '-s', '/tmp/plasma']


/arrow/cpp/src/plasma/store.cc:

This starts up the plasma-mswriter

In [5]:
import subprocess as sp
import time

command_line = ["plasma-mswriter",OUTPUT_FILE]
print(command_line)
mswriter = sp.Popen(command_line)

time.sleep(5)

['plasma-mswriter', '/tmp/new-plasma.ms']
1|2021-08-25T04:16:21.275Z|INFO|MainThread|__init__|processor.py#72||SimpleProcessor waiting for calls at prefix 00000000


### Ok lets launch the receiver


In [6]:
import subprocess as sp
import time
conf_line = "%s" % configfile

exe = "emu-recv"
command_line = [exe,"-c",conf_line]
print(command_line)
recv = sp.Popen(command_line)

time.sleep(5)


['emu-recv', '-c', '/tmp/test_kbyz2iid.conf']


### Now lets  start the transmitter

In [7]:
import subprocess as sp
import signal

conf_line = "%s" % configfile

exe = "emu-send"
command_line = [exe,INPUT_FILE,"-c",conf_line]
print(command_line)


send = sp.run(command_line)
    
    

['emu-send', 'data/sim-vis.ms', '-c', '/tmp/test_kbyz2iid.conf']


If you are sending a single test measurement set. This all ends cleanly - but there is a known feature that if the stream does not end cleanly we need to interupt the writer to ensure the MS is written to disk.

In [8]:




poll=recv.poll()
while (poll):
    print("Receiver still running")
    time.sleep(1)
    #poll.send_signal(signal.SIGINT)
    
print("Receiver done")    

Receiver done


The output measurement set should now also be conformal and be imageable this can be tested by a quick image test.